In [24]:
from __future__ import print_function
import matplotlib
matplotlib.use('Agg')
import matplotlib.pyplot as plt
import pylab
import pandas as pd
import numpy as np
import os
import sys
import gzip
import itertools
import operator
import subprocess
import twobitreader
from Bio.Alphabet import IUPAC
from Bio import SeqIO
from Bio.Seq import Seq
from Bio.SeqRecord import SeqRecord
import pysam
import shutil

from uditas.uditas_replace_helpers import *

In [114]:
#start by making a small working data set of the first 10,000 reads
#each read is 4 lines name, sequence, '+', qualityread

#can check the first 10 lines with the following command 
#!head -10 /media/edanner/NewUbuntuSpace/Workspace/LongReadSequences/Polb_Targeted.fastq

#polb
!head -n40000 /media/edanner/NewUbuntuSpace/Workspace/LongReadSequences/POLB_targeted.fastq >> /media/edanner/NewUbuntuSpace/Workspace/LongReadSequences/First10000/POLB_targ/fastq_files/POLB_targ_R1.fastq
#!head -n40000 /media/edanner/NewUbuntuSpace/Workspace/LongReadSequences/POLB_cntl.fastq >> /media/edanner/NewUbuntuSpace/Workspace/LongReadSequences/First10000/POLB_cntl/fastq_files/POLB_cntl_R1.fastq
#CCNA
#!head -n40000 /media/edanner/NewUbuntuSpace/Workspace/LongReadSequences/CCNA_targeted.fastq >> /media/edanner/NewUbuntuSpace/Workspace/LongReadSequences/First10000/CCNA_targ/fastq_files/CCNA_targ_R1.fastq
#!head -n40000 /media/edanner/NewUbuntuSpace/Workspace/LongReadSequences/CCNA_cntl.fastq >> /media/edanner/NewUbuntuSpace/Workspace/LongReadSequences/First10000/CCNA_cntl/fastq_files/CCNA_cntl_R1.fastq
#LMNA
#!head -n40000 /media/edanner/NewUbuntuSpace/Workspace/LongReadSequences/LMNA_targeted.fastq >> /media/edanner/NewUbuntuSpace/Workspace/LongReadSequences/First10000/LMNA_targ/fastq_files/LMNA_targ_R1.fastq
#!head -n40000 /media/edanner/NewUbuntuSpace/Workspace/LongReadSequences/LMNA_cntl.fastq >> /media/edanner/NewUbuntuSpace/Workspace/LongReadSequences/First10000/LMNA_cntl/fastq_files/LMNA_cntl_R1.fastq

#check file size
#!wc -l filename

In [22]:
!wc -l /media/edanner/NewUbuntuSpace/Workspace/LongReadSequences/CCNA_cntl.fastq

214368 /media/edanner/NewUbuntuSpace/Workspace/LongReadSequences/CCNA_cntl.fastq


#  Pipeline1
# This, for the most part, is the UDITAS pipeline modified to allow for REPLACE targeting. 

## There is a second pipeline below to do global alignments to quantify large deletions, translocatins, concatomers, etc by aligning the sequence past the break site to the entire genome+targeting sequence.

## Inputs
#### next few window are different inputs to make it run well

In [288]:
#inputs

check_plasmid_insertions = 0 #dont do this for longread
ncpu = 4
window_size = 3
amplicon_window_around_cut = 1000
min_MAPQ = 30
min_AS = 3000
process_AMP_seq_run = 0 #off

############# Directory ############
#this is a minimal directory of only ~300 files for quick debugging
directory = '/media/edanner/NewUbuntuSpace/Workspace/LongReadSequences/First10000'

#directory = '/media/edanner/NewUbuntuSpace/Workspace/LongReadSequences'

print(directory)

/media/edanner/NewUbuntuSpace/Workspace/LongReadSequences/First10000


In [342]:
#0 POLB_targeted
#1 POLB_cntl
#2 CCNA_targeted
#3 CCNA_cntl
#4 LMNA_targeted
#5 LMNA_cntl

master_number = 3

#######################################################################################
#primer sequences for mispriming. Primer sequence + 12nt downstream 
#this will only be avialable for read2

##### add the sequence 4 from end of primer and 25ish long in 5'-3>########

primerlist = [['GTCCTTTATTTCAAACCTTATCACA', 'AGATGGCACTTGAAAACTGTTC', 'this is for POLB_targeted (row 0 in sheet)'],
              ['GTCCTTTATTTCAAACCTTATCACA', 'AGATGGCACTTGAAAACTGTTC', 'this is for POLB_cntl (row 1 in sheet)'],
              ['TTTACCCTTCACTCGCCTGCGACCCT', 'CAAAAGATATGATTAAATTAATTGTT', 'this is for CCNA_targeted (row2 in sheet)'],
              ['TTTACCCTTCACTCGCCTGCGACCCT', 'CAAAAGATATGATTAAATTAATTGTT', 'this is for CCNA_cntl (row3 in sheet)'],
              ['AGGTTTTTAAGAAAATAGGACCTTTC', 'ATAAATGATCAACTCCAGTCCTCCTT', 'this is for LMNA_targeted (row 4 in sheet)'],
              ['AGGTTTTTAAGAAAATAGGACCTTTC', 'ATAAATGATCAACTCCAGTCCTCCTT', 'this is for LMNA_cntl (row 5 in sheet']]

                

primer1_seq_plus_downstream = primerlist[master_number][0]
primer2_seq_plus_downstream = primerlist[master_number][1] 
print(primerlist[master_number][2], '\n')    
print('primer1_seq+downstream', primer1_seq_plus_downstream)
print('primer2_seq+downstream', primer2_seq_plus_downstream)


#check what is printed below!!!

#############################################################################################
# Function to make the 'amplicon_info' list. Taking the line of our experiment csv file

def get_csv_data(dir_sample, line_of_data_from_csv):
    sample_info_filename = os.path.join(dir_sample, 'sample_info.csv')
    experiments = pd.read_csv(sample_info_filename)
    return experiments.loc[line_of_data_from_csv]


#the amplicon info is related to the line on the csv file. It is indexed from 0. For PolbF we use 0.
#it is on my extera space so need to make sure that is mounted. (first thing to check if it throws and error)


amplicon_info = get_csv_data(directory, master_number)

###########check waht is printed below #######
#amplicon_info

this is for CCNA_cntl (row3 in sheet) 

primer1_seq+downstream TTTACCCTTCACTCGCCTGCGACCCT
primer2_seq+downstream CAAAAGATATGATTAAATTAATTGTT


In [300]:
# Assign the file_genome_2bit location. This is needed for pulling sequence from the referene genome by location
assembly = amplicon_info['genome']
file_genome_2bit = os.path.join('/media/edanner/NewUbuntuSpace/Workspace/Ref_Genomes', assembly + '.2bit')
print(file_genome_2bit)

# BOWTIE2_INDEXES are needed for global alignments
#not sure if this will work
#normally in bash: export BOWTIE2_INDEXES=/media/edanner/NewUbuntuSpace/Workspace/Ref_Genomes
#check in bash: > ECHO $GENOMES_2BIT

#this is the refrence genome for Bowtie from Illumina. It does not have our targeting vector
%env BOWTIE2_INDEXES=/media/edanner/NewUbuntuSpace/Workspace/Ref_Genomes

#check the env variables
#%env

/media/edanner/NewUbuntuSpace/Workspace/Ref_Genomes/hg38.2bit
env: BOWTIE2_INDEXES=/media/edanner/NewUbuntuSpace/Workspace/Ref_Genomes


In [281]:
###########################
#
#   my homemade function to make a fastq with only correct priming events that 
#   I currently have skipped making this becasue a relitivly high amount are on target due to nested and I just want results
#   this should be a similiar function to the demultiplex sorting function but simpler
#   the sequence to align is the first reads of r2
#######################

def correct_priming_longread_2primer(dir_sample, amplicon_info, primer1_seq_plus_downstream, primer2_seq_plus_downstream, length_shortest_primer, length_to_search=45):
    
    #list of 9mers from the downstream sequence of the 
    downstream1_list, downstream2_list = [], []
    i, j = 0, 0
    while i < (len(primer1_seq_plus_downstream)-9): 
        downstream1_list.append(primer1_seq_plus_downstream[i:i+9])
        i += 2    
    while j < (len(primer2_seq_plus_downstream)-9): 
        downstream2_list.append(primer2_seq_plus_downstream[j:j+9])
        j += 2
    
    
    #define the input files and output files
    N7 = amplicon_info['index_I1']
    N5 = amplicon_info['index_I2']
    
    #input files
    r1_fastq = create_filename(dir_sample, N7, N5, 'R1fastq')
    #output files not gz compressed
    file_R1_corrprime = create_filename(dir_sample, N7, N5, 'R1fastq_CorrPrime')

    #mismatched files
    file_out_r1_not_corrprime = os.path.join(dir_sample, N7 + '_' + N5, 'fastq_files', 'mis_prime_R1.fastq')

    #open/create all these files
    ref_file_R1_corrprime = open(file_R1_corrprime, "w")
    ref_file_out_r1_not_corrprime = open(file_out_r1_not_corrprime, "w")
    
    starting_base = length_shortest_primer-6
    ending_base = starting_base + length_to_search
    
    # We open r1 files and distribute reads/fastq
    with open_fastq_or_gz(r1_fastq) as r1_file:
        # Add counters for all reads

        reads_in_experiment_list_count = 0
        reads_misprimed = 0
        reads_good_prime = 0
     
        for header in r1_file:

            reads_in_experiment_list_count += 1
                
            seq_r1 = r1_file.next()
            r1_file.next()
            qual_r1 = r1_file.next()

            #We mask with N any bases with scores below or equal to , (11, default in mask)
            # I had to make a find in string function becauase pacbio has a lot of errors and 1st base 
            # often random and moves around so you can't use hamming distance
            
            seq_side1 = mask(seq_r1[starting_base:ending_base], qual_r1[starting_base:ending_base])
            seq_side2 = mask(seq_r1[-ending_base:-starting_base], qual_r1[-ending_base:-starting_base])
            seq_side2_rev_comp = reverse_complement(seq_side2)
            # change to 1 for reads with perfect match or match within hamming distance decided above
            is_good_read = 0
            
            side1_primer1 = any(x in seq_side1 for x in downstream1_list)
            side1_primer2 = any(x in seq_side1 for x in downstream2_list)
            side2_primer1 = any(x in seq_side2_rev_comp for x in downstream1_list)
            side2_primer2 = any(x in seq_side2_rev_comp for x in downstream2_list)
            
            if side1_primer1 == True and side2_primer2 == True:
                is_good_read = 1
            elif side1_primer2  == True and side2_primer1 == True:
                is_good_read = 1
                       
            #Print good reads 
            if is_good_read:
                reads_good_prime += 1
                # We test whether the read has on of the combination of indices from our experiment list
                # If not save in a separate file
                r1f = ref_file_R1_corrprime
                print("\n".join([header.strip(),seq_r1.strip(),"+",qual_r1.strip()]), file=r1f)

            else:
                print("\n".join([header.strip(), seq_r1.strip(), "+", qual_r1.strip()]), file=ref_file_out_r1_not_corrprime)
                reads_misprimed += 1
                
        print('reads_in_experiment_list_count', reads_in_experiment_list_count)
        print('reads with good priming:', reads_good_prime)
        print('reads misprimed', reads_misprimed)

In [312]:
#sort for correct priming. This is very important for longer amplicons
correct_priming_longread_2primer(directory, amplicon_info, primer1_seq_plus_downstream, primer2_seq_plus_downstream, 25)

reads_in_experiment_list_count 10000
reads with good priming: 9044
reads misprimed 956


In [313]:
get_reaction_type(amplicon_info)

'replace'

In [343]:
create_amplicon(directory, amplicon_info, file_genome_2bit)

In [206]:
############################
#
# Aligns reads globally to amplicon. "end-to-end" as the default function in bowtie2
# Input: directory to be analyzed
#        amplicon_info, slice of sample_info.csv for the sample being processed
#        file_genome_2bit, 2bit file with the reference genome being used
#
# ##########################
def align_amplicon_longread(dir_sample, amplicon_info):

    # We first check if the experiment had any guides
    N7 = amplicon_info['index_I1']
    N5 = amplicon_info['index_I2']
    
    #inputfile
    file_R1 = create_filename(dir_sample, N7, N5, 'R1fastq_CorrPrime') #don't use trimmed
    if not os.path.exists(os.path.dirname(file_R1)):
        os.mkdir(os.path.dirname(file_R1))
    
    #Sam
    file_sam_amplicons = create_filename(dir_sample, N7, N5, 'sam_amplicons')
    file_sam_report_amplicons = create_filename(dir_sample, N7, N5, 'sam_report_amplicons')    
    if not os.path.exists(os.path.dirname(file_sam_amplicons)):
        os.mkdir(os.path.dirname(file_sam_amplicons))
    
    #Bam
    file_bam_amplicons = create_filename(dir_sample, N7, N5, 'bam_amplicons')
    file_sorted_bam_amplicons = create_filename(dir_sample, N7, N5, 'sorted_bam_amplicons')
    if not os.path.exists(os.path.dirname(file_bam_amplicons)):
        os.mkdir(os.path.dirname(file_bam_amplicons))

    # global alignment to the amplicons with bowtie2
    initial_dir = os.getcwd()
    folder_amplicons = create_filename(dir_sample, N7, N5, 'amplicons')
    
    os.chdir(folder_amplicons)

    minimap2_command = ['minimap2', '-a', 'Hk11', '-r2500', "amplicons.fa", file_R1, ">", file_sam_amplicons]
    minimaprun = " ".join(minimap2_command)
    print(minimaprun)
    
    !{minimaprun}
    
    #handle_sam_report_amplicons = open(file_sam_report_amplicons, 'wb')

    #subprocess.call(minimap2_command, stderr=handle_sam_report_amplicons)

    #handle_sam_report_amplicons.close()

    # convert sam to bam
    sam_to_bam_amplicons_command = ['samtools', 'view', '-Sb', file_sam_amplicons]

    handle_file_bam_amplicons = open(file_bam_amplicons, 'wb')

    subprocess.call(sam_to_bam_amplicons_command, stdout=handle_file_bam_amplicons)

    # sort bam files
    sort_bam_amplicons_command = ['samtools', 'sort', file_bam_amplicons, '-o', file_sorted_bam_amplicons]
    subprocess.call(sort_bam_amplicons_command)

    # Clean up
    #os.remove(file_sam_amplicons)
    #os.remove(file_bam_amplicons)

    # Create bam index files
    create_bam_amplicons_index_command = ['samtools', 'index', file_sorted_bam_amplicons]
    subprocess.call(create_bam_amplicons_index_command)

    os.chdir(initial_dir)

In [344]:
align_amplicon_longread(directory, amplicon_info)

minimap2 -ax map-pb -r2500 amplicons.fa /media/edanner/NewUbuntuSpace/Workspace/LongReadSequences/First10000/CCNA_cntl/fastq_files/CCNA_cntl_R1.CorrPrime.fastq > /media/edanner/NewUbuntuSpace/Workspace/LongReadSequences/First10000/CCNA_cntl/sam_amplicon_files/CCNA_cntl.sam
[M::mm_idx_gen::0.002*1.39] collected minimizers
[M::mm_idx_gen::0.006*0.77] sorted minimizers
[M::main::0.006*0.77] loaded/built the index for 14 target sequence(s)
[M::mm_mapopt_update::0.006*0.78] mid_occ = 19
[M::mm_idx_stat] kmer size: 19; skip: 10; is_hpc: 1; #seq: 14
[M::mm_idx_stat::0.006*0.78] distinct minimizers: 519 (4.24% are singletons); average occurrences: 8.004; average spacing: 8.039
[M::worker_pipeline::6.687*2.85] mapped 9244 sequences
[M::main] Version: 2.17-r941
[M::main] CMD: minimap2 -ax map-pb -r2500 amplicons.fa /media/edanner/NewUbuntuSpace/Workspace/LongReadSequences/First10000/CCNA_cntl/fastq_files/CCNA_cntl_R1.CorrPrime.fastq
[M::main] Real time: 6.687 sec; CPU: 19.026 sec; Peak RSS: 0.08

In [268]:
################################################################################
#  Function to analyze indels and structural rearrangements from aligned reads to amplicons
################################################################################
def analyze_alignments_longread(dir_sample, amplicon_info, window_size, amplicon_window_around_cut, min_MAPQ, min_AS):

    reaction_type = get_reaction_type(amplicon_info)

    # UDiTaS primer strand
    strand = amplicon_info['strand']

    N7 = amplicon_info['index_I1']
    N5 = amplicon_info['index_I2']
    exp_dir = create_filename(dir_sample, N7, N5, 'mainfolder')
    results_folder = os.path.join(exp_dir, 'results')
    if not os.path.exists(results_folder):
        os.mkdir(results_folder)

    results_file = (create_filename(dir_sample, N7, N5, 'results_amplicons') + '_results_amplicon_window_'
                    + str(window_size) + '.xlsx')

    file_sorted_bam_amplicons = create_filename(dir_sample, N7, N5, 'sorted_bam_amplicons')


    #this analysis assumed barcodes and it was easier to amke a fake barcode set and ignore the data than fix everythign
    UMI_dict = create_fake_barcode_dict(dir_sample, amplicon_info)

    filename_amplicons_fa = os.path.join(exp_dir, 'amplicons', 'amplicons.fa')

    results_df = pd.DataFrame(index=[0])

    # We get the reference amplicon list
    with open(filename_amplicons_fa, "rU") as handle:
        records = list(SeqIO.parse(handle, "fasta"))
    #first we get fine the cut sites for each fasta amplicon
    for record in records:
        cut_df = get_cut_in_reference_amplicon_df(amplicon_info, reaction_type, record, strand, window_size,
                                                  amplicon_window_around_cut)
        print(cut_df)
        # We go over cut1 and cut2 and when using cut1 we check if we are in control sample
        for i in cut_df.index:
            cut = cut_df.loc[i, 'cut_type']
            print("cut type", cut)
            cut_position = cut_df.loc[i, 'cut_position']
            print("cut_position", cut_position)

            region_chr = record.name
            print("region_chr", region_chr)

            region_start = cut_position - window_size
            region_end = cut_position + window_size + 1

            results = find_indels(file_sorted_bam_amplicons, strand, region_chr, region_start, region_end, UMI_dict, min_MAPQ, min_AS)
            # This is to catch the control case, no cut there
            if len(cut) > 0:
                prefix = region_chr + '_' + cut
            else:
                prefix = region_chr

            results_df[prefix + '_total_reads'] = [results[0]]
            results_df[prefix + '_total_indels'] = [results[1]]
            results_df[prefix + '_total_deletions'] = [results[2]]
            results_df[prefix + '_total_insertions'] = [results[3]]


    median_size = analyze_fragment_sizes(dir_sample, amplicon_info, min_MAPQ)
    results_df['median_fragment_size'] = [median_size]

    results_df.to_excel(results_file)
    return results_df

In [291]:
#################################################################################
# Function to create barcode dict
#################################################################################
def create_fake_barcode_dict(dir_sample, amplicon_info):
    
    N7 = amplicon_info['index_I1']
    N5 = amplicon_info['index_I2']
    
    #input files
    r1_fastq = create_filename(dir_sample, N7, N5, 'R1fastq')

    barcode_dict = dict()
    
    with open_fastq_or_gz(r1_fastq) as r1_file:    
        for header in r1_file:
                
            seq_r1 = r1_file.next()
            r1_file.next()
            qual_r1 = r1_file.next()

            #We mask with N any bases with scores below or equal to , (11, default in mask)
            # I had to make a find in string function becauase pacbio has a lot of errors and 1st base 
            # often random and moves around so you can't use hamming distance
            
            barcode1 = seq_r1[1:10]
            quality = qual_r1[1:10]
               
            barcode_dict[header] = [barcode1.rstrip(), quality.rstrip()]

    return barcode_dict

In [289]:
def find_indels(bam_file, strand, region_chr, region_start, region_end, UMI_dict, min_MAPQ, min_AS):
    bam_in_alignment_file = pysam.AlignmentFile(bam_file, 'rb')

    # We get the reads that overlap the window in which we make the counts
    # fetch will get reads with any overlap with the window
    # For UDiTaS, care must be take to ensure that the read covers the whole window, some short reads may cover just
    # one side of the window, depending on the direction of the UDiTaS primer
    bam_in = bam_in_alignment_file.fetch(region_chr, region_start, region_end)

    names_list = []
    position_list = []
    indel_list = []
    UMI_list = []
    for read in bam_in:
        # We add here a check to make sure the read came from the primer, crossed the cut and covered the whole window
        if read.has_tag('AS'):
            read_AS = read.get_tag('AS')
        # We test first if the read is unmapped, otherwise read_AS would be undefined
        if not read.is_unmapped and (((read.reference_start < region_start) and
                 (read.reference_end > region_end)) and
                    read.mapping_quality >= min_MAPQ and
                    read_AS >= min_AS and  not read.is_secondary):
            read_indels = parse_indels(read)
            # if no indels found, write 0
            if len(read_indels) == 0:
                read_indels.append(('-', 0))

            for pos, indel in read_indels:
                names_list.append(read.query_name)
                if pos == '-':
                    position_list.append(-1)
                else:
                    position_list.append(int(pos))

                indel_list.append(indel)
                #UMI_list.append(UMI_dict[read.query_name][0])

    df = pd.DataFrame({'read_name': names_list,
                       'position': position_list,
                       'indel': indel_list})#,
                       #'UMI': UMI_list})

    df['position_end'] = df.position + np.abs(df.indel)

    overlap = [get_intersection(df.loc[index]['position'], df.loc[index]['position_end'], region_start, region_end)
               for index in range(df.shape[0])]

    position_filter = np.array(overlap) > 0
    deletion_filter = position_filter & np.array(df.indel < 0)
    insertion_filter = position_filter & np.array(df.indel > 0)

    total_reads_in_region = len(set(df['read_name']))
    total_indels = len(set(df.loc[position_filter]['read_name']))
    total_deletions = len(set(df.loc[deletion_filter]['read_name']))
    total_insertions = len(set(df.loc[insertion_filter]['read_name']))

    return [total_reads_in_region, total_indels, total_deletions, total_insertions]



In [294]:
def parse_indels(aligned_read):
    indels = []

    if not aligned_read.is_unmapped and not aligned_read.is_secondary:  # We only look at primary alignments
        ref_i = aligned_read.reference_start
        for operation, length in aligned_read.cigartuples:
            if operation == 0:
                ref_i += length
            elif operation == 1:
                indels.append((ref_i, length))
            elif operation == 2:
                indels.append((ref_i, -length))
                ref_i += length
            else:
                print('Unrecognized CIGAR operation for:', aligned_read.query_name , file=sys.stderr)
    print("parsed indel:", indels)
    return indels

In [345]:
analyze_alignments_longread(directory, amplicon_info, window_size, amplicon_window_around_cut, min_MAPQ, min_AS)

  cut_type cut_position
0     cut1         1000
1     cut2         1720
cut type cut1
cut_position 1000
region_chr wt
parsed indel: [(1329, -1)]
parsed indel: []
parsed indel: [(34, -1), (106, -1), (177, 1), (253, -1), (400, -1), (602, -1), (973, -1), (1221, -1), (1476, -1), (2705, 1)]
parsed indel: []
parsed indel: [(1540, 1), (1547, -1)]
parsed indel: [(1329, -1)]
parsed indel: [(129, -1)]
parsed indel: [(229, -1), (257, -1), (439, -1), (521, -1), (697, -1), (859, -1), (1606, 1)]
parsed indel: [(129, 2), (439, -1), (807, -1), (1145, 1), (1238, -1), (2228, -1)]
parsed indel: [(34, -1), (2697, 1)]
parsed indel: [(1329, -1), (1363, -1)]
parsed indel: []
parsed indel: [(1038, -1), (1363, -1)]
parsed indel: [(129, 1)]
parsed indel: [(1599, -1), (1833, -1)]
parsed indel: [(129, 1), (165, -1), (944, -1)]
parsed indel: []
parsed indel: [(1599, -1)]
parsed indel: [(400, -1), (1011, -1), (1231, -1), (1476, -1), (2013, -1)]
parsed indel: [(1303, 1)]
parsed indel: [(129, 1), (1476, -1)]
parsed i

Unrecognized CIGAR operation for: m54099_190108_235709/4915382/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/4915382/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/4915812/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/4915812/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/4915927/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/4915927/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/5111964/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/5111964/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/5112349/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/5112349/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/5177754/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/5177754/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/5177963/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/5177963/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/5178145

Unrecognized CIGAR operation for: m54099_190108_235709/8126935/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/8126972/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/8126972/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/8127014/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/8127014/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/8127036/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/8127036/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/8127233/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/8127233/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/8127238/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/8127238/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/8127241/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/8127241/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/8127249/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/8127249

parsed indel: [(155, 1), (429, -1), (439, -1), (533, 1), (583, -1), (643, -1), (696, -1), (938, 1), (988, -1), (1038, 1), (1097, 1), (1329, 1), (1363, 1), (1476, -1), (1726, -1), (1763, -1), (1786, 1), (1962, -1), (2295, 1), (2520, -1), (2709, 1)]
parsed indel: [(129, -1), (1610, -1)]
parsed indel: [(129, -1)]
parsed indel: [(910, -1), (1085, 1), (1114, -1), (1476, -1), (1839, -1)]
parsed indel: [(129, -1), (1476, -1)]
parsed indel: [(129, 1)]
parsed indel: [(21, 1), (400, -1), (429, -1), (467, -1), (815, -1), (1094, -1), (1213, -1), (1286, -1), (1513, -1), (1536, -1), (1547, -1), (1863, -1), (2033, -1), (2179, -1)]
parsed indel: [(113, 1), (129, 1), (154, 1), (631, 1), (766, 1), (807, 1), (933, 1), (1102, 1), (1221, 1), (1286, 2), (1320, 1), (1329, 1), (1363, 1), (1399, 1), (1453, 1), (1512, 1), (1520, 1), (1547, 1), (1756, 1), (1973, -1), (2061, 1), (2080, 1), (2277, 1), (2361, 1), (2552, 1), (2554, 1), (2703, 1)]
parsed indel: [(910, -1), (1857, -1)]
parsed indel: [(611, -1)]
parsed

m54099_190108_235709/9371794/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/9371794/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/9371810/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/9371810/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/9371851/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/9371851/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/9372098/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/9372098/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/9372141/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/9372141/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/9372144/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/9372144/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/9372308/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/9372308/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/9372499/ccs
Unrecognized CIGAR operation 

...

Unrecognized CIGAR operation for: m54099_190108_235709/39715275/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/39715275/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/39715370/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/39715370/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/39715372/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/39715372/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/39715375/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/39715375/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/39715417/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/39715417/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/39715455/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/39715455/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/39715536/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/39715536/ccs
Unrecognized CIGAR operation for: m54099_190108_

parsed indel: [(129, -1), (234, 1), (1476, -1), (1756, -1)]
parsed indel: [(26, 1), (283, -1), (659, 1), (751, -1), (891, -2), (1017, -1), (1063, -1), (1231, 1), (1476, 1), (1991, 1), (2056, 1), (2075, -1), (2333, 1), (2506, 1), (2582, 1), (2603, 1), (2605, 1)]
parsed indel: [(287, -1), (487, 1), (1542, 1), (2013, -1)]
parsed indel: [(47, 1), (53, -1), (68, 1), (106, 1), (119, 1), (129, 1), (262, -1), (283, 1), (324, -1), (360, 1), (392, -1), (420, 2), (439, -1), (489, 1), (510, 1), (538, 3), (562, 1), (571, 1), (672, -1), (695, 1), (711, -1), (764, -1), (807, 1), (815, 1), (847, -1), (876, -1), (986, -1), (1038, -1), (1099, 1), (1191, -1), (1229, -1), (1259, 1), (1308, -1), (1339, -1), (1407, 1), (1409, -1), (1450, -1), (1464, 1), (1469, 1), (1476, 2), (1520, 1), (1525, -1), (1566, -1), (1596, 1), (1605, 1), (1607, -1), (1631, -1), (1651, -1), (1688, -1), (1698, 1), (1726, -1), (1756, -1), (1815, -1), (1823, -1), (1839, -1), (1845, -1), (1853, 1), (1919, 1), (1943, 1), (1964, 2), (211

Unrecognized CIGAR operation for: m54099_190108_235709/40764372/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/40764372/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/40829096/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/40829096/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/40829149/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/40829149/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/40829155/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/40829155/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/40829251/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/40829251/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/40829287/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/40829287/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/40829294/ccs
Unrecognized CIGAR operation for: m54099_190108_235709/40829294/ccs
Unrecognized CIGAR operation for: m54099_190108_

  cut_type cut_position
0     cut1         1000
cut type cut1
cut_position 1000
region_chr large_deletion
  cut_type cut_position
0     cut1         1000
1     cut2         1720
cut type cut1
cut_position 1000
region_chr large_inversion
cut type cut2
cut_position 1720
region_chr large_inversion
  cut_type cut_position
0     cut1         1000
1     cut2         2256
cut type cut1
cut_position 1000
region_chr replace_fwd
cut type cut2
cut_position 2256
region_chr replace_fwd
  cut_type cut_position
0     cut1         1000
1     cut2         2256
cut type cut1
cut_position 1000
region_chr replace_rev
cut type cut2
cut_position 2256
region_chr replace_rev
  cut_type cut_position
0     cut1         1256
cut type cut1
cut_position 1256
region_chr hiti_5prime_replace_exon_fwd
  cut_type cut_position
0     cut1         1256
cut type cut1
cut_position 1256
region_chr hiti_5prime_replace_exon_rev
  cut_type cut_position
0     cut1          720
cut type cut1
cut_position 720
region_chr hiti_3prim

wt_cut1_total_reads  wt_cut1_total_indels  wt_cut1_total_deletions  \
0                 9244                   115                       32   

   wt_cut1_total_insertions  wt_cut2_total_reads  wt_cut2_total_indels  \
0                        85                 9244                    93   

   wt_cut2_total_deletions  wt_cut2_total_insertions  \
0                        6                        87   

   large_deletion_cut1_total_reads  large_deletion_cut1_total_indels  ...  \
0                                0                                 0  ...   

   doner_head_head_cut1_total_insertions  1a_1a_cut1_total_reads  \
0                                      0                       0   

   1a_1a_cut1_total_indels  1a_1a_cut1_total_deletions  \
0                        0                           0   

   1a_1a_cut1_total_insertions  2b_2b_cut1_total_reads  \
0                            0                       0   

   2b_2b_cut1_total_indels  2b_2b_cut1_total_deletions  \
0                        0                           0   

   2b_2b_cut1_total_insertions  median_fragment_size  
0                            0                     0  

[1 rows x 73 columns]

In [296]:
len('ACTGGGGTTCAATTTTCTGTGTCCTTTATTTCAAACCTTATCACATGGTATTCATTTGTTTTTCATTTTCTGCTTTTTACTTTATCTTTTAGTGATTTGGTAAGCATTATATTCATATGACTTTTATATTTCTAATTTTCCATGTAGCCTGGAGTAGGAACAAAAATTGCTGAAAAGATTGATGAGTTTTTAGCAACTGGAAAATTACGTAAACTGGAAAAGGTAAAATTTTAACTTGTTTACTTCATTAATTATAGTATCTGCCTTTATGGCCACTATGTAGCGTCATTGCAGGGTGACCAATGTCATTCACTGTAGTGAGACTCACAGGAAATGAGGTGAGTGAAGTTGATGGCTTTAACTTTTTGAATGTTATTTCCATAAAATGTTCACTTGTTTTATGTGGCATTTAAGAGACTATTAACACCCGTAATAGAGTTGGCTCATCGTTTTCAGTACTATTCAGAAAAGAGATTATAAACTTTGACTGAAAGATCGTTATCTTTTAGAATTTCTTTATTTCTTTATTTATGTTTTTGAGATGGAGTCTTGCTCTGTCGCCCAGGCTGGAGTGCAGTGGCGCGATCTCGGCTCACTGCAAGCTCCGCCTCCTGGGTTCATGCCATTCTCCTGCCTCAGCCTCCTGAGTAGCTGGGACTACAGGCGCCCGCCACCACACCCAGCTAATTTTTTGCATTTTTAGTAGAGACGGGGTTTCACCATGTTAGCCAGTATGGTCTCGATCTCCTGACCTCGTGATCTGCCCGCCTCGGCCTCCCAAAGTGCTGGGATTACAGGCATGAGCCACCATACCCGGCCATCTTTTAGAATTTCTATGTTTACACTCACCCAAGCATTTTTATGGTTTTATTTCACCCCATGATAGTAATTATATCACTTCTGATCTGTTAAGAATAGACCTTTTAAAAGTATTGGATAACTTAGAGATGAGACATCTTCAGTTACTCTGTTATTCACCTATTACTCCTTAGGTTACTTGTGAATAATTTTGTGTGGGTCACCCAGGCAAATGTAAATAGCTCTTCATGTCTTTTAGCAGACTGGTATGTTTCCAATAAGATCATTTAAGTCCTCAAAGCATTCCTAAATCATTGTTAGACTTTTTTTTTTTCTTAAAGATTCGGCAGGATGATACGAGTTCATCCATCAATTTCCTGACTCGAGTTAGTGGCATTGGGTAAGAACTATTTTTTAAGCAGACACAATCGTCAGTTAGTTTATTTTTCCTGTTAGCCAAAGTAAATTACATGCTGTTTCTCAAAACCTGTACTTCACCACCTCTGTACCTTAGCCATACAGTTCACCCTTCCATAGCTTATGATCTGAGGCCGATTCTTCAGATAGTGTCTCTACTGTAAGGTCCCCATCCAAGGCAGATGTTACCTCCTTCATGAAACCAGTTTGGTTACCCAGGCAGAAAGAACCTCTCCCTCCTCTGAACTCCACTACCATTTCCTCCGTGTGCATCTATTTCCTGCTCCAGCTTGGCCTCTTTTGTTTCTCTGAGCATGATATTTATCATAGCACCTCATGAATTTGGAACAAGCCCTCAAGCTTTTTTTAAATTATTTTTTGAGACAGGGTTGCTATGTTGCCCATGCTGGTCTTGAACTCCTGGGCTTAAGTGATTCTTCCTCCTCAGCATCCCGAGTAGCTTGGATTATAGGTGCACGCCCCCTTGCCCAGCTTCAAGCATTTTTAAATGAAGGGATTATTATCTTAAAATTTGAGCTGGTACCAAGGTGGGCTTTTTTGACACTGGCTGAAGTAAAGATTAACATTGAAATATTAAGGCTTTAGTGCTCTCATCTTTATGGCATGGGGCATTCCTTTAAATATAATGATTTGTTCTTTAAATGGCAGCATTTTCGGTGAAAGTTATTCTAAAACATATTAAATTCTTAAACCTAGTATGTTGAAAATGAAAATGACTGCTTGGGGACTCAAGGCCATTATAAAATTTTCATTGGAAGAATTACAAAAATTTTTTTTTTTTAGAGATAGTGTCTTATTCTGCTATCTAGGCTAGAGTGCAGTGGTGCTATTATAGCTCACTGTAACCTTGAACTCTTGGGGTAAAGTGACTCTCCTGCCTTAGTACTCCTTTTGAGTAGCTGAGACTACAGGCTTGCGCAACCATGTGTGGCCAATTTTTGTATCTTTTGTAGAGAAGAGGTCTCCCTATGTTGCCTAGGCTGGTCTTGAACTCCTGGCCTCAAGCCTTCCTCCCACTTAAGCCTCCCAGAGTGCTAGGATTATAGGTGTGAACCACAAGGTGTTTTAGAGAGCATCTATTATCCTTTTTTTCTAGGCAAGAGAACTGAAAGTTGAATATAGAACATGAGTAACCATGGCAGAGCCAGATTTGAAACCCATATCTTCTGACTCCGAGTTCAGTTCTGTTTCTTCTATGCTGCATTGCCTTCCTAACATCAGTATCAGTTTCTATATCACAATATAATGTGATGATATTTGCATAGCTTACTGAATGATACAGGTTTATTTGTCCCGAAACACTGTGGCCCCAGACTATTGTGCTTGTATGTTTATATGTGTGTGTATGCATTTCTTTCTGTTCACCGCTCCTGCTTTATTATGCTGTAAACTGGTATGGTGAGAAGAGAGTCAGGAAATCTGGATAATGGTCTAGAGCTAGCACCAGCTAGATTTGTGACCTTAGCAAATCACTTCATCTTTCTAGGTTTCAGTGTCCTTCCTTATGAAATAAGAGAGAAATTTGGTTAATCAGTAAGCTTCCTTCTGTCCCCATCCTATAAGAGCATCTTCAGTCATTTCTGACATTCTGATTTATTTATATGAATAAAGTGATATTTTAGAAACCTAAATCAGATTTTATCATTGCTTTGTGCAGTGTCCTCTAATAGCTTTCCATTGCACTCAGAATAAAATCCAAACCTATCACCATGGCTCTAAAAGCACAGTAGAGTGTAACACCTGCGTACTGTTCCATAGCACCTCATACCGTCACTTACATCACTCTATGCATCCTAGTTTTTCTCTTCTCTTGAACAGGCCAAGCTCATGCCAGCCTTAGGGCCCTTGCACTAATTGTTTCCTTTTCCCGAAACGTTTTTATCTTTGATCCCCTAGATAGCTGGTTCTTTAGTCATTCAAACCTCAGCTTAGATACCATCTCAGAGACCTTCTACCACTCAGTCTAAAGTAGGACCCAGCCATTCTGTCATATTCTATTTTAATTTATCCATCTGATTTTTTCTTGTTTATGTAACTAACTATTGTCTCTATCTACCCACTTACATTCTTATTCCTGCTACATTTTCAGCACCCAGGAAAGTATCTGACACATAATGGCCCTCAGTAAATCTTAGTTCAATGAATGAACAGTTTTCAAGTGCCATCTGTACATGGGCACTATGACAGC')

3424

In [273]:
################################################################################
# Function to calculate the number of reads and collapsed reads aligned to the reference amplicons
        # this doesn't tell you which type or where
# litterally just gives 2 numbers. Number of amplicons that were aligned and the number after collapse. Doesn't break it down by alignment to any particular amplicon
################################################################################
def analyze_alignments_all_amplicons_longread(dir_sample, amplicon_info, min_MAPQ, min_AS):
    N7 = amplicon_info['index_I1']
    N5 = amplicon_info['index_I2']

    exp_dir = create_filename(dir_sample, N7, N5, 'mainfolder')

   
    
    ## THIS was added to get an idea of how many unique reads there are.
    
    results_folder = os.path.join(exp_dir, 'results')
    if not os.path.exists(results_folder):
        os.mkdir(results_folder)

    results_file = create_filename(dir_sample, N7, N5, 'results_all_amplicons')

    file_sorted_bam_amplicons = create_filename(dir_sample, N7, N5, 'sorted_bam_amplicons')

    bam_in_alignment_file = pysam.AlignmentFile(file_sorted_bam_amplicons, 'rb')
    bam_in_all = bam_in_alignment_file.fetch()
    names_list_amplicons = []

    for read in bam_in_all:
        if read.has_tag('AS'):
            read_AS = read.get_tag('AS')
        # We test first if the read is unmapped, otherwise read_AS would be undefined
        if not read.is_unmapped and read.mapping_quality >= min_MAPQ \
                and read_AS >= min_AS and not read.is_secondary:
            names_list_amplicons.append(read.query_name)

    all_amplicons_total_reads = len(set(names_list_amplicons))

    results_df = pd.DataFrame({'all_amplicons_total_reads': [all_amplicons_total_reads]},
                              columns=['all_amplicons_total_reads'])

    results_df.to_excel(results_file)

    return results_df

In [346]:
result_reads_in_all_amplicons_df = analyze_alignments_all_amplicons_longread(directory, amplicon_info, min_MAPQ, min_AS)
result_reads_in_all_amplicons_df

all_amplicons_total_reads
0                       9244

## Summarize Data
